This first section loads up the necessary packages and defines a few things, also reads in the profile data

In [25]:
import pandas as pd
import xarray as xr
import datashader as ds
import datashader.transfer_functions as tf
from datashader.bokeh_ext import InteractiveImage

from IPython.core.display import HTML, display

import bokeh.plotting as bp
from bokeh.plotting import figure, show, output_file, gridplot, hplot
from bokeh.models import HoverTool, ColumnDataSource, OpenURL, TapTool, Rect, Range1d
from bokeh.models.widgets import Panel, Tabs

from collections import OrderedDict

import os

bp.output_notebook()

raw = pd.read_csv('dummydata/raw.csv')
highlights = pd.read_csv('dummydata/highlights.csv')
highlights.tail()

x_range=(min(raw["X"]),max(raw["X"]))
y_range=(min(raw["Y"]),max(raw["Y"]))

   
options = dict(line_color='blue')

display(HTML("<style>.container { width:90% !important; }</style>"))


Loading BokehJS ...

In [23]:
rawsource = ColumnDataSource(raw)
highsource = ColumnDataSource(highlights)

TOOLS="resize,crosshair,pan,wheel_zoom,box_zoom,undo,redo,reset,tap,previewsave,box_select,poly_select,lasso_select,hover"

In [24]:
def create_image(x_range=x_range, y_range=y_range, w=500, h=500):
    cvs = ds.Canvas(x_range=x_range, y_range=y_range, plot_height=h, plot_width=w)
    agg = cvs.line(raw, 'X', 'Y', agg=ds.any())
    return tf.interpolate(agg)


def base_plot(tools='pan,wheel_zoom,reset'):
    p = bp.figure(tools=TOOLS, plot_width=500, plot_height=500,
        x_range=x_range, y_range=y_range, outline_line_color=None,
        min_border=0, min_border_left=0, min_border_right=0,
        min_border_top=0, min_border_bottom=0)   
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    return p

In [28]:
s1 = bp.figure(tools=TOOLS, plot_width=500, plot_height=500,
        outline_line_color=None,
        min_border=0, min_border_left=0, min_border_right=0,
        min_border_top=0, min_border_bottom=0)   

s1.scatter(x='A', y='B',source=highsource,fill_color='black',line_color=None,size=10)
hover = s1.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([('X', "@X"),('Y',"@Y"),("Name","@Name")])


s2 = bp.figure(tools=TOOLS, plot_width=500, plot_height=500,
        outline_line_color=None,
        min_border=0, min_border_left=0, min_border_right=0,
        min_border_top=0, min_border_bottom=0)   

s2.scatter(x='Age', y='Height',source=highsource,fill_color='red',line_color=None,size=10)
hover = s2.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([('A', "@A"),('B',"@B"),("Name","@Name")])

s = hplot(s1,s2)
show(s)
#For whatever reason, the bokeh plot has to go before the interactive image or the int image wont appear.

p = base_plot()

p.scatter(x='X', y='Y',source=highsource,fill_color='black',line_color=None)
hover = p.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([('Age', "@Age"),('Height',"@Height"),('Name',"@Name")])

InteractiveImage(p, create_image, throttle=200)
